
# Arc Mobility Model

This example demonstrates the BrownianArcMobilityModel which calculates arc displacement
due to Brownian motion and thermal effects.


In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import openmdao.api as om

from paroto.models.arc_mobility import BrownianArcMobilityModel

# Create OpenMDAO problem
prob = om.Problem()
prob.model.add_subsystem("mobility", BrownianArcMobilityModel())
prob.setup()

# Set parameters for typical operating conditions
prob.set_val("mobility.pulse_frequency", 50e3)  # 50 kHz
prob.set_val("mobility.sustainer_pulse_duration", 100e-6)  # 100 μs
prob.set_val("mobility.gap_distance", 0.01)  # 10 mm
prob.set_val("mobility.arc_current", 1000.0)  # 1000 A
prob.set_val("mobility.preheat_temperature", 300.0)  # K

# Run model
prob.run_model()

# Extract results
disp_rms = prob.get_val("mobility.arc_displacement_rms")[0]
mobility_factor = prob.get_val("mobility.mobility_factor")[0]
spread_factor = prob.get_val("mobility.thermal_spread_factor")[0]

print("=" * 50)
print("Arc Mobility Model - Brownian Motion")
print("=" * 50)
print(f"RMS Displacement: {disp_rms * 1e3:.2f} mm")
print(f"Mobility Factor: {mobility_factor:.2f}")
print(f"Thermal Spread Factor: {spread_factor:.2f}")
print("=" * 50)
print(f"Arc moves ~{disp_rms * 1e3:.2f} mm during off-time")
print(f"This spreads thermal load over {spread_factor:.1f}x larger area")
print("=" * 50)

# Plot arc displacement vs pulse frequency
print("\nGenerating plot: Arc Displacement vs Pulse Frequency...")
freq_range = np.logspace(3, 6, 50)  # 1 kHz to 1 MHz
disp_values = []
spread_values = []

for freq in freq_range:
    prob.set_val("mobility.pulse_frequency", freq)
    prob.run_model()
    disp_values.append(prob.get_val("mobility.arc_displacement_rms")[0] * 1e3)  # mm
    spread_values.append(prob.get_val("mobility.thermal_spread_factor")[0])

fig, (ax1, ax2) = plt.subplots(2, 1, figsize=(8, 8))

# Plot 1: RMS Displacement
ax1.loglog(freq_range / 1e3, disp_values, "b-", linewidth=2)
ax1.axvline(x=50, color="g", linestyle=":", alpha=0.7, label="Nominal (50 kHz)")
ax1.set_xlabel("Pulse Frequency (kHz)")
ax1.set_ylabel("RMS Displacement (mm)")
ax1.set_title("Arc Displacement vs Pulse Frequency")
ax1.grid(True, alpha=0.3, which="both")
ax1.legend()

# Plot 2: Thermal Spread Factor
ax2.semilogx(freq_range / 1e3, spread_values, "r-", linewidth=2)
ax2.axvline(x=50, color="g", linestyle=":", alpha=0.7, label="Nominal (50 kHz)")
ax2.set_xlabel("Pulse Frequency (kHz)")
ax2.set_ylabel("Thermal Spread Factor")
ax2.set_title("Thermal Load Spreading vs Pulse Frequency")
ax2.grid(True, alpha=0.3)
ax2.legend()

plt.tight_layout()
plt.show()